In [ ]:
%%capture
!gdown --id 1ZEmMGZCBsfeeFrrJs2uUHK8mzzuNkzTR
!pip install transformers
!pip install simpletransformers

In [ ]:
import pandas as pd
import numpy as np
import re
from sklearn.model_selection import train_test_split
import os
import spacy
import simpletransformers
import sklearn

In [ ]:
def annotate_sentence(s):
    #Annotates Sentence by replacing words with respective tags and the rest with Os
    #Example Input: <TREAT> Intravenous immune globulin </TREAT> for <DIS> recurrent spontaneous abortion </DIS> .
    #Example Output: ['B-TREAT', 'I-TREAT', 'I-TREAT', O, 'B-DIS', 'I-DIS', 'I-DIS', O]
    s = s.split(' ')
    subtag = []
    for x in range(len(s)):
        m = re.match('<(.*?)>', s[x])
        if m:
            subtag.append([x, m.group(1).replace('/', '')])
    subtag_index =  [[x[0], y[0], reduce_tag(x[1])] for x, y in zip(subtag[::2], subtag[1::2])]
    subtag_loc = [x[0] for x in subtag]
    replaced = []
    for x in subtag_index:
        for z,y in enumerate(range(x[0]+1, x[1]),1):
            s[y] = f"{'B' if z == 1 else 'I'}-{x[2]}"
            replaced.append(y)
    replaced_tags = replaced + subtag_loc
    retag = [y for y in [x for x in range(len(s))] if y not in replaced_tags]
    for x in retag:
        s[x] = 'O'
    for x in subtag_loc[::-1]:
        del s[x]
    return s
    
def reduce_tag(x):
    return 'DIS' if 'DIS' in x else 'TREAT' if 'TREAT' in x else None
def clean_labels(data):
    """
    Take raw dataframe and blend labels together. Remove TO_SEE instances.
    Input:
        Data: Pandas Dataframe
    Output:
        Data: Pandas Dataframe
    """
    data = data[data['Label'] != 'TO_SEE']
    label_dict = {'NONE': 'NONE', 'DISONLY': 'OTHER', 'TREATONLY': 'OTHER', 'PREVENT': 'PREVENT', 'VAGUE': 'OTHER', 'TO_SEE': 'OTHER',
       'TREAT_FOR_DIS': 'CURE', 'SIDE_EFF': 'SIDE_EFF', 'TREAT_NO_FOR_DIS': 'NO_CURE'}
    data = data.replace({'Label': label_dict})
    return data
with open('sentences_with_roles_and_relations.txt', encoding = "ISO-8859-1") as f:      #Read in Data
    lines = f.readlines()

def clean_data(sentence):
  tokens = sentence.split()
  for token in tokens:
    if(re.match('<.*?>',token)):
      tokens.remove(token)
  for token in tokens:
    if(re.match('<.*?>',token)):
      tokens.remove(token)
  return tokens

#sp = spacy.load('en_core_web_sm')
def add_pos_tags(sentence):
  pos_tags = []
  sen = sp(sentence)
  for i in range(0,len(sen)):
    pos_tags.append(sen[i].pos_)
  return pos_tags

def remove_labels(sentence):
  sentence = re.sub('<.*?>', '',sentence)
  sentence = re.sub('[ \t]+',' ',sentence)
  sentence = sentence.replace(' .','.')
  return sentence.strip()


In [ ]:
data_df = pd.DataFrame({'Data':lines})                                                  #Convert to Dataframe
data_df['Label'] = data_df['Data'].apply(lambda x: x.split('||')[1].replace('\n', ''))  #Split Label into new column - Y1 Input
data_df['Data'] = data_df['Data'].apply(lambda x: x.split('||')[0].strip())             #Split Data into new column
data_df['Clean Sentence'] = data_df['Data'].apply(lambda x:remove_labels(x))
data_df['Data_Clean'] = data_df['Data'].apply(lambda x: clean_data(x)) #Remove Tags from Data into new column - X Input
data_df['Annot'] = data_df['Data'].apply(lambda x: annotate_sentence(x))                #Annotate Sentences - Y2 Input
data_df['Data'].iloc[872] = '<TREATONLY> Primary thrombolytic treatment </TREATONLY> ( within 24 hours of diagnosis ) was given to 169 patients ( 23.5 % ) , whereas the remaining 550 patients were initially treated with <TREATONLY> heparin </TREATONLY> alone .'
#data_df['POS'] = data_df['Data'].apply(lambda x: add_pos_tags(x))
data_df = clean_labels(data_df)

label_map = {'NONE':0,"OTHER":1,'PREVENT':2,'CURE':3,'SIDE_EFF':4,'NO_CURE':5}
data_df.replace({'Label':label_map},inplace=True)

In [ ]:
def replace_with_tags(sentence, annotation):
  new_sentence = []
  new_annotation = []
  for i in range(len(annotation)):
    if annotation[i] == 'O':
      new_sentence.append(sentence[i])
      new_annotation.append(annotation[i])
    elif annotation[i][:1] == 'B':
      new_sentence.append(f'@{annotation[i][2:]}$')
      new_annotation.append(annotation[i])
  new_sentence = ' '.join(new_sentence)
  new_sentence = new_sentence.replace(' .','.')
  new_sentence = new_sentence.replace(' ,',',')
  new_sentence = new_sentence.replace(' !','!')
  new_sentence = new_sentence.replace(' ?','?')
  new_sentence = new_sentence.replace(' ;',';')
  return new_sentence
data_df['Tagged_sentence'] = data_df.apply(lambda x: replace_with_tags(x['Data_Clean'], x['Annot']), axis = 1)
data_df_class = data_df[['Tagged_sentence', 'Label']]
data_df_class.reset_index(drop=True, inplace=True)
data_df_class.columns = ['text', 'labels']

In [ ]:
from simpletransformers.classification import ClassificationModel, ClassificationArgs

In [ ]:
train_df, test_df = train_test_split(data_df_class, test_size=0.2, random_state=0)
test_df, dev_df = train_test_split(test_df, test_size=0.5, random_state=0)

In [ ]:
model_args = ClassificationArgs(num_train_epochs=10)

In [ ]:
model = ClassificationModel('bert','bert-large-cased',num_labels=6,args=model_args) 

Downloading:   0%|          | 0.00/762 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.25G [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-large-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at 

Downloading:   0%|          | 0.00/208k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/426k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

In [ ]:
model.train_model(train_df)

  0%|          | 0/2864 [00:00<?, ?it/s]

Epoch:   0%|          | 0/10 [00:00<?, ?it/s]

Running Epoch 0 of 10:   0%|          | 0/358 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:134: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


Running Epoch 1 of 10:   0%|          | 0/358 [00:00<?, ?it/s]

...

Running Epoch 6 of 10:   0%|          | 0/358 [00:00<?, ?it/s]

Running Epoch 7 of 10:   0%|          | 0/358 [00:00<?, ?it/s]

Running Epoch 8 of 10:   0%|          | 0/358 [00:00<?, ?it/s]

Running Epoch 9 of 10:   0%|          | 0/358 [00:00<?, ?it/s]

(3580, 0.13231662804021516)

In [ ]:
y_true = []
y_pred = []
for i in range(0,len(dev_df)):
  predictions, raw_outputs = model.predict([dev_df.iloc[i]['text']])
  y_pred.append(predictions[0])
  y_true.append(dev_df.iloc[i]['labels'])

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
len(y_pred)

358

In [ ]:
len(y_true)

358

In [ ]:
sklearn.metrics.accuracy_score(y_pred,y_true)

0.9748603351955307

## Error Analysis

In [ ]:
from collections import Counter

In [ ]:
Counter(y_true)

Counter({0: 183, 1: 82, 2: 3, 3: 85, 4: 5})

In [ ]:
Counter(y_pred)

Counter({0: 183, 1: 86, 2: 4, 3: 84, 4: 1})

In [ ]:
output = pd.DataFrame(list(zip(*[y_true,y_pred])))
output.rename(columns={0:'y_true',1:'y_pred'},inplace=True)
output.to_csv('bert_tagged_output.csv', index=False)

In [ ]:
y_pred[0:20]

[1, 0, 0, 3, 0, 1, 0, 3, 3, 0, 1, 0, 0, 0, 1, 1, 0, 0, 0, 1]

In [ ]:
y_true[0:20]

NameError: ignored

In [ ]:
def accuracies_by_class(value):
  pred_indices = [i for i, x in enumerate(y_pred) if x == value]
  true_indices = [i for i, x in enumerate(y_true) if x == value]

  if(len(pred_indices)==0):
    return 0
  return len(set(pred_indices) & set(true_indices))/len(pred_indices)

In [ ]:
accuracies_by_class(4)

0